In [1]:
import pandas as pd
import requests
from itertools import chain
import pickle
import numpy as np
import matplotlib.pyplot as plt
import time
import sys
import glob
import os
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm import tqdm
import math

In [2]:
with open('count_measures_dict_0822.pkl','rb') as file:
    dict = pickle.load(file)

In [3]:
author_list = list(dict.keys())

In [53]:
len(author_list)

84194

In [6]:
test = dict[author_list[0]]

In [8]:
test.columns

Index(['publication_month', 'count', 'af_count', '2023 JIF_sum',
       '2023 JIF_mean', '2023 JIF_median', 'JIF Percentile_count_q1',
       'JIF Percentile_q1_ratio', 'JIF Percentile_median', '5 Year JIF_sum',
       '5 Year JIF_mean', '5 Year JIF_median',
       '5 Year JIF Quartile_q_count_q1', '5 Year JIF Quartile_q_q1_ratio',
       'JIF Without Self Cites_sum', 'JIF Without Self Cites_mean',
       'JIF Without Self Cites_median', 'Immediacy Index_sum',
       'Immediacy Index_mean', 'Immediacy Index_median', '2023 JCI_sum',
       '2023 JCI_mean', '2023 JCI_median', 'JCI Percentile_count_q1',
       'JCI Percentile_q1_ratio', 'JCI Percentile_median', 'Eigenfactor_sum',
       'Eigenfactor_mean', 'Eigenfactor_median', 'Normalized Eigenfactor_sum',
       'Normalized Eigenfactor_mean', 'Normalized Eigenfactor_median',
       'Article Influence Score_sum', 'Article Influence Score_mean',
       'Article Influence Score_median', 'AIS Quartile_q_count_q1',
       'AIS Quartile_q_q1_

In [9]:
test['publication_month'].iloc[0]

'2013-11'

In [11]:
test[test['publication_month']<='2024-07']

publication_month  count  af_count  2023 JIF_sum  2023 JIF_mean  \
0           2013-11      1         0           0.0            NaN   
1           2016-08      1         0           0.5            0.5   
2           2017-12      1         0           1.2            1.2   
3           2022-07      1         1           2.8            2.8   
4           2023-11      1         0          13.6           13.6   
5           2024-06      1         0           3.0            3.0   

   2023 JIF_median  JIF Percentile_count_q1  JIF Percentile_q1_ratio  \
0              NaN                        0                      NaN   
1              0.5                        1                      1.0   
2              1.2                        1                      1.0   
3              2.8                        1                      1.0   
4             13.6                        1                      1.0   
5              3.0                        1                      1.0   

   JIF Percentile_median  5 Year JIF_sum  ...  AIS Quartile_q_q1_ratio  \
0                    NaN             0.0  ...                      NaN   
1                   18.0             0.9  ...                      0.0   
2                   36.3             1.0  ...                      0.0   
3                   55.8             3.3  ...                      0.0   
4                   99.7            13.6  ...                      1.0   
5                   86.3             3.1  ...                      0.0   

   authors_count_sum  authors_count_mean  authors_count_median  \
0                  1                 1.0                   1.0   
1                  5                 5.0                   5.0   
2                  2                 2.0                   2.0   
3                  5                 5.0                   5.0   
4                  5                 5.0                   5.0   
5                  1                 1.0                   1.0   

   countries_distinct_count_sum  countries_distinct_count_mean  \
0                           0.0                            0.0   
1                           1.0                            1.0   
2                           1.0                            1.0   
3                           1.0                            1.0   
4                           5.0                            5.0   
5                           1.0                            1.0   

   countries_distinct_count_median  institutions_distinct_count_sum  \
0                              0.0                              0.0   
1                              1.0                              1.0   
2                              1.0                              1.0   
3                              1.0                              3.0   
4                              5.0                              8.0   
5                              1.0                              1.0   

   institutions_distinct_count_mean  institutions_distinct_count_median  
0                               0.0                                 0.0  
1                               1.0                                 1.0  
2                               1.0                                 1.0  
3                               3.0                                 3.0  
4                               8.0                                 8.0  
5                               1.0                                 1.0  

[6 rows x 46 columns]

In [13]:
test[test['af_count']>0].publication_month.min()

'2022-07'

In [19]:
print('a')
test['publication_month'] = pd.to_datetime(test['publication_month'], format='%Y-%m')
complete_monthly_series(test)

a


publication_month  count  af_count  2023 JIF_sum  2023 JIF_mean  \
0          2013-11-01    1.0       0.0           0.0            NaN   
1          2013-12-01    NaN       NaN           NaN            NaN   
2          2014-01-01    NaN       NaN           NaN            NaN   
3          2014-02-01    NaN       NaN           NaN            NaN   
4          2014-03-01    NaN       NaN           NaN            NaN   
..                ...    ...       ...           ...            ...   
123        2024-02-01    NaN       NaN           NaN            NaN   
124        2024-03-01    NaN       NaN           NaN            NaN   
125        2024-04-01    NaN       NaN           NaN            NaN   
126        2024-05-01    NaN       NaN           NaN            NaN   
127        2024-06-01    1.0       0.0           3.0            3.0   

     2023 JIF_median  JIF Percentile_count_q1  JIF Percentile_q1_ratio  \
0                NaN                      0.0                      NaN   
1                NaN                      NaN                      NaN   
2                NaN                      NaN                      NaN   
3                NaN                      NaN                      NaN   
4                NaN                      NaN                      NaN   
..               ...                      ...                      ...   
123              NaN                      NaN                      NaN   
124              NaN                      NaN                      NaN   
125              NaN                      NaN                      NaN   
126              NaN                      NaN                      NaN   
127              3.0                      1.0                      1.0   

     JIF Percentile_median  5 Year JIF_sum  ...  AIS Quartile_q_q1_ratio  \
0                      NaN             0.0  ...                      NaN   
1                      NaN             NaN  ...                      NaN   
2                      NaN             NaN  ...                      NaN   
3                      NaN             NaN  ...                      NaN   
4                      NaN             NaN  ...                      NaN   
..                     ...             ...  ...                      ...   
123                    NaN             NaN  ...                      NaN   
124                    NaN             NaN  ...                      NaN   
125                    NaN             NaN  ...                      NaN   
126                    NaN             NaN  ...                      NaN   
127                   86.3             3.1  ...                      0.0   

     authors_count_sum  authors_count_mean  authors_count_median  \
0                  1.0                 1.0                   1.0   
1                  NaN                 NaN                   NaN   
2                  NaN                 NaN                   NaN   
3                  NaN                 NaN                   NaN   
4                  NaN                 NaN                   NaN   
..                 ...                 ...                   ...   
123                NaN                 NaN                   NaN   
124                NaN                 NaN                   NaN   
125                NaN                 NaN                   NaN   
126                NaN                 NaN                   NaN   
127                1.0                 1.0                   1.0   

     countries_distinct_count_sum  countries_distinct_count_mean  \
0                             0.0                            0.0   
1                             NaN                            NaN   
2                             NaN                            NaN   
3                             NaN                            NaN   
4                             NaN                            NaN   
..                            ...                            ...   
123                           NaN                       

In [22]:
with open('ls_authors.pkl','rb') as file:
    ls_authors = pickle.load(file)
with open('ls_first_authors.pkl','rb') as file:
    ls_first_authors = pickle.load(file)
with open('ls_last_authors.pkl','rb') as file:
    ls_last_authors = pickle.load(file)

In [ ]:
print('a')
def process_dataframe(key, df):
    if df['publication_month'].dtype == 'O':
        df = df[df['publication_month'] <= '2024-07']
        df = df[df['publication_month'].str[:4] >= '1900']
        df['publication_month'] = pd.to_datetime(df['publication_month'], format='%Y-%m')
    else:
        df = df[df['publication_month'] <= pd.to_datetime('2024-07-01')]
    
    if len(df[df['af_count'] > 0]) == 0:
        return None
    
    df = df[['publication_month', 'count', 'af_count', '2023 JIF_sum', '5 Year JIF_sum',
             'Immediacy Index_sum', '2023 JCI_sum', 'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
             'Article Influence Score_sum', 'authors_count_sum', 'countries_distinct_count_sum',
             'institutions_distinct_count_sum']]
    
    df['publication_month'] = pd.to_datetime(df['publication_month'], format='%Y-%m')
    first_af = df[df['af_count'] > 0].publication_month.min()
    
    if first_af < pd.to_datetime('2021-07-01'):
        return None
    
    df.loc[:, 'treatment_month'] = first_af
    df.loc[:, 'id'] = key
    df['is_ls'] = key in ls_authors
    df['is_ls_first'] = key in ls_first_authors
    df['is_ls_last'] = key in ls_last_authors
    df['start_month'] = df['publication_month'].min()
    df['end_month'] = df['publication_month'].max()
    
    return df

def main():
    combined_df = pd.DataFrame()
    
    with ThreadPoolExecutor() as executor:
        futures = []
        for key, df in dict.items():
            future = executor.submit(process_dataframe, key, df)
            futures.append(future)
        
        for future in tqdm(as_completed(futures), total=len(futures), desc="Processing DataFrames"):
            result = future.result()
            if result is not None:
                combined_df = pd.concat([combined_df, result])
    
    return combined_df

if __name__ == "__main__":
    combined_df = main()
    with open('combined_df_0827.pkl','wb') as file:
        pickle.dump(combined_df, file)

a


Processing DataFrames:   4%|▍         | 3587/84194 [02:37<1:04:37, 20.79it/s]

In [54]:
combined_df

publication_month  count  af_count  2023 JIF_sum  5 Year JIF_sum  \
0         2011-01-01      1         0           0.0             0.0   
1         2012-04-01      1         0           2.6             2.8   
2         2012-08-01      1         0           1.7             1.6   
3         2014-06-01      1         0           2.4             3.3   
4         2017-10-01      1         0           0.0             0.0   
..               ...    ...       ...           ...             ...   
43        2024-02-01      1         0           8.1             9.8   
44        2024-03-01      2         0          10.2            11.3   
45        2024-05-01      1         0          31.7            36.6   
46        2024-06-01      2         0          20.3            22.3   
47        2024-07-01      2         0          17.1            21.4   

    Immediacy Index_sum  2023 JCI_sum  Eigenfactor_sum  \
0                   0.0          0.00            0.000   
1                   0.4          0.83            0.005   
2                   0.7          0.49            0.000   
3                   0.7          0.79            0.003   
4                   0.0          0.00            0.000   
..                  ...           ...              ...   
43                  2.2          1.58            0.092   
44                  1.8          2.62            0.015   
45                  4.4          8.81            0.139   
46                  6.7          3.08            0.032   
47                  5.5          4.88            0.025   

    Normalized Eigenfactor_sum  Article Influence Score_sum  \
0                        0.000                        0.000   
1                        1.084                        0.511   
2                        0.095                        0.306   
3                        0.621                        0.442   
4                        0.000                        0.000   
..                         ...                          ...   
43                      20.064                        4.380   
44                       3.402                        2.089   
45                      30.403                       20.125   
46                       6.961                        8.024   
47                       5.563                        5.455   

    authors_count_sum  countries_distinct_count_sum  \
0                 2.0                           0.0   
1                 6.0                           1.0   
2                 6.0                           2.0   
3                 4.0                           1.0   
4                 2.0                           0.0   
..                ...                           ...   
43                8.0                           2.0   
44               14.0                           2.0   
45               50.0                           9.0   
46               24.0                           6.0   
47                4.0                           2.0   

    institutions_distinct_count_sum treatment_month  \
0                               0.0      2023-12-01   
1                               3.0      2023-12-01   
2                               3.0      2023-12-01   
3                               1.0      2023-12-01   
4                               0.0      2023-12-01   
..                              ...             ...   
43                              3.0      2023-06-01   
44                              6.0      2023-06-01   
45                             30.0      2023-06-01   
46                             13.0      2023-06-01   
47                              2.0      2023-06-01   

                                  id  is_ls  is_ls_first  is_ls_last  \
0   https://openalex.org/A5100774045  False        False       False   
1   https://openalex.org/A5100774045  False        False       False   
2   https://openalex.org/A5100774045  False        False       False   
3   https://openalex.org/A5100774045  False        False       False   
4   https://op

In [55]:
del dict

In [2]:
print('a')
with open('topics_array_dict.pkl','rb') as file:
    topics_dict = pickle.load(file)

a


In [162]:
topic_df = pd.DataFrame()
for key,value in topics_dict.items():
    df = value['portfolio']
    df.loc[:,'id'] = key
    df['portfolio_sum'] = df['portfolio'].cumsum()
    df.loc[:,'topic_max'] = value['topics'][np.argmax(df['portfolio_sum'].iloc[-1])]
    topic_df = pd.concat([topic_df,df])

with open('topic_df.pkl','wb') as file:
    pickle.dump(topic_df, file)

{'topics': ['Epidemiology and Pathogenesis of Respiratory Viral Infections',
  'Epilepsy and Seizures',
  'Genomic Rearrangement Disorders in Skin Diseases',
  'Glycosylation in Health and Disease',
  'Neonatal Brain Injury and Developmental Consequences'],
 'num_topics': 5,
 'portfolio':   publication_month        portfolio
 0           2013-11  [0, 0, 0, 0, 1]
 1           2016-08  [0, 1, 0, 0, 0]
 2           2017-12  [0, 0, 1, 0, 0]
 3           2022-07  [0, 0, 0, 1, 0]
 4           2023-11  [1, 0, 0, 0, 0]
 5           2024-06  [0, 0, 0, 0, 1]}

In [8]:
print('a')
def process_topic(key, value):
    if value['num_topics'] == 0:
        return None
    df = value['portfolio'].copy()
    df['id'] = key
    df['portfolio_sum'] = df['portfolio'].cumsum()
    df['topic_max'] = value['topics'][np.argmax(df['portfolio_sum'].iloc[-1])]
    return df

def process_topics(topics_dict):
    with ThreadPoolExecutor() as executor:
        futures = [executor.submit(process_topic, key, value) for key, value in topics_dict.items()]
        
        # Process results as they complete
        dfs = []
        for future in tqdm(as_completed(futures), total=len(topics_dict), desc="Processing topics"):
            df = future.result()
            if df is not None:
                dfs.append(df)
    
    # Concatenate all DataFrames at once
    topic_df = pd.concat(dfs, ignore_index=True)
    return topic_df

# Assume topics_dict is already defined
topic_df = process_topics(topics_dict)

# Save the result
with open('topic_df.pkl', 'wb') as file:
    pickle.dump(topic_df, file)

print("Processing complete and results saved.")

a


Processing topics: 100%|██████████| 84194/84194 [00:58<00:00, 1431.60it/s] 


Processing complete and results saved.


In [10]:
del topics_dict

In [11]:
print('a')
with open('subfields_array_dict.pkl','rb') as file:
    subfields_dict = pickle.load(file)

a


In [12]:
print('a')
def process_subfield(key, value):
    if value['num_subfields'] == 0:
        return None
    df = value['portfolio'].copy()
    df['id'] = key
    df['portfolio_sum'] = df['portfolio'].cumsum()
    df['subfield_max'] = value['subfields'][np.argmax(df['portfolio_sum'].iloc[-1])]
    return df

def process_subfields(subfields_dict):
    with ThreadPoolExecutor() as executor:
        futures = [executor.submit(process_subfield, key, value) for key, value in subfields_dict.items()]
        
        # Process results as they complete
        dfs = []
        for future in tqdm(as_completed(futures), total=len(subfields_dict), desc="Processing subfields"):
            df = future.result()
            if df is not None:
                dfs.append(df)
    
    # Concatenate all DataFrames at once
    subfield_df = pd.concat(dfs, ignore_index=True)
    return subfield_df

# Assume subfields_dict is already defined
subfield_df = process_subfields(subfields_dict)

# Save the result
with open('subfield_df.pkl', 'wb') as file:
    pickle.dump(subfield_df, file)

print("Processing complete and results saved.")

a


Processing subfields: 100%|██████████| 84194/84194 [00:57<00:00, 1464.42it/s]


Processing complete and results saved.


In [13]:
del subfields_dict

In [14]:
print('a')
with open('fields_array_dict.pkl','rb') as file:
    fields_dict = pickle.load(file)

a


In [15]:
print('a')
def process_field(key, value):
    if value['num_fields'] == 0:
        return None
    df = value['portfolio'].copy()
    df['id'] = key
    df['portfolio_sum'] = df['portfolio'].cumsum()
    df['field_max'] = value['fields'][np.argmax(df['portfolio_sum'].iloc[-1])]
    return df

def process_fields(fields_dict):
    with ThreadPoolExecutor() as executor:
        futures = [executor.submit(process_field, key, value) for key, value in fields_dict.items()]
        
        # Process results as they complete
        dfs = []
        for future in tqdm(as_completed(futures), total=len(fields_dict), desc="Processing fields"):
            df = future.result()
            if df is not None:
                dfs.append(df)
    
    # Concatenate all DataFrames at once
    field_df = pd.concat(dfs, ignore_index=True)
    return field_df

# Assume fields_dict is already defined
field_df = process_fields(fields_dict)

# Save the result
with open('field_df.pkl', 'wb') as file:
    pickle.dump(field_df, file)

print("Processing complete and results saved.")

a


Processing fields: 100%|██████████| 84194/84194 [00:48<00:00, 1738.55it/s] 


Processing complete and results saved.


In [16]:
del fields_dict

In [17]:
print('a')
with open('domains_array_dict.pkl','rb') as file:
    domains_dict = pickle.load(file)

a


In [18]:
print('a')
def process_domain(key, value):
    if value['num_domains'] == 0:
        return None
    df = value['portfolio'].copy()
    df['id'] = key
    df['portfolio_sum'] = df['portfolio'].cumsum()
    df['domain_max'] = value['domains'][np.argmax(df['portfolio_sum'].iloc[-1])]
    return df

def process_domains(domains_dict):
    with ThreadPoolExecutor() as executor:
        futures = [executor.submit(process_domain, key, value) for key, value in domains_dict.items()]
        
        # Process results as they complete
        dfs = []
        for future in tqdm(as_completed(futures), total=len(domains_dict), desc="Processing domains"):
            df = future.result()
            if df is not None:
                dfs.append(df)
    
    # Concatenate all DataFrames at once
    domain_df = pd.concat(dfs, ignore_index=True)
    return domain_df

# Assume domains_dict is already defined
domain_df = process_domains(domains_dict)

# Save the result
with open('domain_df.pkl', 'wb') as file:
    pickle.dump(domain_df, file)

print("Processing complete and results saved.")

a


Processing domains: 100%|██████████| 84194/84194 [00:45<00:00, 1837.92it/s] 


Processing complete and results saved.


In [20]:
del domains_dict

In [22]:
domain_df['domain_max'].unique()

array(['Life Sciences', 'Health Sciences', 'Physical Sciences',
       'Social Sciences'], dtype=object)

In [25]:
domain_df[domain_df['domain_max']=='Life Sciences']['id'].nunique()/domain_df['id'].nunique()

0.572387492277717

In [28]:
domain_df[domain_df['domain_max']=='Social Sciences']['id'].nunique()/domain_df['id'].nunique()

0.00856579385068669

In [29]:
field_df['field_max'].unique()

array(['Medicine', 'Agricultural and Biological Sciences',
       'Biochemistry, Genetics and Molecular Biology',
       'Immunology and Microbiology', 'Computer Science', 'Engineering',
       'Chemistry', 'Environmental Science', 'Arts and Humanities',
       'Neuroscience', 'Physics and Astronomy', 'Materials Science',
       'Earth and Planetary Sciences', 'Social Sciences',
       'Chemical Engineering', 'Dentistry', 'Nursing',
       'Business, Management and Accounting',
       'Pharmacology, Toxicology and Pharmaceutics', 'Energy',
       'Psychology', 'Decision Sciences', 'Health Professions',
       'Economics, Econometrics and Finance', 'Veterinary', 'Mathematics'],
      dtype=object)

In [31]:
with open('combined_df_0827.pkl','rb') as file:
    combined_df = pickle.load(file)

In [39]:
topic_df

publication_month                                          portfolio  \
0              1999-01-01  [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1              2002-01-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2              2002-11-01  [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, ...   
3              2004-01-01  [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, ...   
4              2005-01-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                   ...                                                ...   
3944029        2024-05-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3944030        2024-06-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3944031        2024-07-01  [0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3944032        2024-08-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
3944033        2024-11-01  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                       id  \
0        https://openalex.org/A5101884287   
1        https://openalex.org/A5101884287   
2        https://openalex.org/A5101884287   
3        https://openalex.org/A5101884287   
4        https://openalex.org/A5101884287   
...                                   ...   
3944029  https://openalex.org/A5100422786   
3944030  https://openalex.org/A5100422786   
3944031  https://openalex.org/A5100422786   
3944032  https://openalex.org/A5100422786   
3944033  https://openalex.org/A5100422786   

                                             portfolio_sum  \
0        [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1        [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2        [0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, ...   
3        [0, 0, 0, 2, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, ...   
4        [0, 0, 0, 2, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, ...   
...                                                    ...   
3944029  [6, 1, 1, 4, 3, 1, 8, 4, 2, 1, 1, 1, 2, 1, 2, ...   
3944030  [6, 1, 1, 4, 3, 1, 8, 4, 2, 1, 1, 1, 2, 1, 2, ...   
3944031  [6, 1, 1, 4, 3, 1, 9, 4, 2, 1, 1, 1, 2, 1, 2, ...   
3944032  [6, 1, 1, 4, 3, 1, 9, 4, 2, 1, 1, 1, 2, 1, 2, ...   
3944033  [6, 1, 1, 4, 3, 1, 9, 4, 2, 1, 1, 1, 2, 1, 2, ...   

                                                 topic_max  
0        Statistical Machine Translation and Natural La...  
1        Statistical Machine Translation and Natural La...  
2        Statistical Machine Translation and Natural La...  
3        Statistical Machine Translation and Natural La...  
4        Statistical Machine Translation and Natural La...  
...                                                    ...  
3944029  DNA Nanotechnology and Bioanalytical Applications  
3944030  DNA Nanotechnology and Bioanalytical Applications  
3944031  DNA Nanotechnology and Bioanalytical Applications  
3944032  DNA Nanotechnology and Bioanalytical Applications  
3944033  DNA Nanotechnology and Bioanalytical Applications  

[3942862 rows x 5 columns]

In [41]:
topic_df = topic_df[topic_df['publication_month'].str[:4]>='1900']
topic_df['publication_month'] = pd.to_datetime(topic_df['publication_month'])
topic_df = topic_df.rename(columns={'portfolio':'topic_portfolio','portfolio_sum':'topic_portfolio_sum'})

In [42]:
combined_df = combined_df.merge(topic_df, on=['id','publication_month'], how='left')

In [44]:
subfield_df = subfield_df[subfield_df['publication_month'].str[:4]>='1900']
subfield_df['publication_month'] = pd.to_datetime(subfield_df['publication_month'])
subfield_df = subfield_df.rename(columns={'portfolio':'subfield_portfolio','portfolio_sum':'subfield_portfolio_sum'})
combined_df = combined_df.merge(subfield_df, on=['id','publication_month'], how='left')

In [45]:
field_df = field_df[field_df['publication_month'].str[:4]>='1900']
field_df['publication_month'] = pd.to_datetime(field_df['publication_month'])
field_df = field_df.rename(columns={'portfolio':'field_portfolio','portfolio_sum':'field_portfolio_sum'})
combined_df = combined_df.merge(field_df, on=['id','publication_month'], how='left')

In [46]:
domain_df = domain_df[domain_df['publication_month'].str[:4]>='1900']
domain_df['publication_month'] = pd.to_datetime(domain_df['publication_month'])
domain_df = domain_df.rename(columns={'portfolio':'domain_portfolio','portfolio_sum':'domain_portfolio_sum'})
combined_df = combined_df.merge(domain_df, on=['id','publication_month'], how='left')

/state/partition1/job-50331405/ipykernel_1300424/2649340914.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  domain_df['publication_month'] = pd.to_datetime(domain_df['publication_month'])


In [48]:
with open('combined_df_0828.pkl','wb') as file:
    pickle.dump(combined_df, file)

In [51]:
del topic_df
del subfield_df
del field_df
del domain_df

In [53]:
combined_df = combined_df.drop(columns={'topic_portfolio','subfield_portfolio','field_portfolio','domain_portfolio'})

In [54]:
combined_df

publication_month  count  af_count  2023 JIF_sum  5 Year JIF_sum  \
0              2011-01-01      1         0           0.0             0.0   
1              2012-04-01      1         0           2.6             2.8   
2              2012-08-01      1         0           1.7             1.6   
3              2014-06-01      1         0           2.4             3.3   
4              2017-10-01      1         0           0.0             0.0   
...                   ...    ...       ...           ...             ...   
3929319        2024-02-01      1         0           8.1             9.8   
3929320        2024-03-01      2         0          10.2            11.3   
3929321        2024-05-01      1         0          31.7            36.6   
3929322        2024-06-01      2         0          20.3            22.3   
3929323        2024-07-01      2         0          17.1            21.4   

         Immediacy Index_sum  2023 JCI_sum  Eigenfactor_sum  \
0                        0.0          0.00            0.000   
1                        0.4          0.83            0.005   
2                        0.7          0.49            0.000   
3                        0.7          0.79            0.003   
4                        0.0          0.00            0.000   
...                      ...           ...              ...   
3929319                  2.2          1.58            0.092   
3929320                  1.8          2.62            0.015   
3929321                  4.4          8.81            0.139   
3929322                  6.7          3.08            0.032   
3929323                  5.5          4.88            0.025   

         Normalized Eigenfactor_sum  Article Influence Score_sum  ...  \
0                             0.000                        0.000  ...   
1                             1.084                        0.511  ...   
2                             0.095                        0.306  ...   
3                             0.621                        0.442  ...   
4                             0.000                        0.000  ...   
...                             ...                          ...  ...   
3929319                      20.064                        4.380  ...   
3929320                       3.402                        2.089  ...   
3929321                      30.403                       20.125  ...   
3929322                       6.961                        8.024  ...   
3929323                       5.563                        5.455  ...   

         start_month  end_month  \
0         2011-01-01 2024-05-01   
1         2011-01-01 2024-05-01   
2         2011-01-01 2024-05-01   
3         2011-01-01 2024-05-01   
4         2011-01-01 2024-05-01   
...              ...        ...   
3929319   2010-10-01 2024-07-01   
3929320   2010-10-01 2024-07-01   
3929321   2010-10-01 2024-07-01   
3929322   2010-10-01 2024-07-01   
3929323   2010-10-01 2024-07-01   

                                       topic_portfolio_sum  \
0        [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
1        [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2        [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, ...   
3        [0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, ...   
4        [1, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, ...   
...                                                    ...   
3929319  [1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, ...   
3929320  [1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 2, 1, 1, 1, ...   
3929321  [1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 2, 1, 1, 1, ...   
3929322  [1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 3, 1, 1, 1, ...   
3929323  [1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 4, 1, 1, 1, ...   

                                                 topic_max  \
0        Biological Activities of Phenothiazines and Re...   
1        Biological Activities of Phenothiazines and Re...   
2        Biological Activities of Phenothiazines and Re...   
3        Biological Activities of Phenothiazine

In [2]:
def hhi(x):
    if np.sum(x)==0:
        return np.nan
    return float(np.sum(np.square(x))/np.square(np.sum(x)))

In [57]:
combined_df['topic_hhi_total'] = combined_df['topic_portfolio_sum'].apply(hhi)
combined_df['subfield_hhi_total'] = combined_df['subfield_portfolio_sum'].apply(hhi)
combined_df['field_hhi_total'] = combined_df['field_portfolio_sum'].apply(hhi)
combined_df['domain_hhi_total'] = combined_df['domain_portfolio_sum'].apply(hhi)

In [60]:
with open('combined_df_0828.pkl','wb') as file:
    pickle.dump(combined_df, file)

In [3]:
with open('combined_df_0828.pkl', 'rb') as file:
    combined_df = pickle.load(file)

In [3]:
print(combined_df['start_month'].min())
print(combined_df['end_month'].max())

1900-01-01 00:00:00
2024-07-01 00:00:00


In [10]:
(combined_df['end_month'] - combined_df['start_month'])

0         13 days 08:09:12.328767123
1         13 days 08:09:12.328767123
2         13 days 08:09:12.328767123
3         13 days 08:09:12.328767123
4         13 days 08:09:12.328767123
                     ...            
3929319   13 days 18:12:49.315068493
3929320   13 days 18:12:49.315068493
3929321   13 days 18:12:49.315068493
3929322   13 days 18:12:49.315068493
3929323   13 days 18:12:49.315068493
Length: 3929324, dtype: timedelta64[ns]

In [11]:
combined_df[combined_df['start_month']>=pd.to_datetime('1950-01-01')].id.nunique()

81712

In [19]:
combined_df.columns

Index(['publication_month', 'count', 'af_count', '2023 JIF_sum',
       '5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum',
       'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
       'Article Influence Score_sum', 'authors_count_sum',
       'countries_distinct_count_sum', 'institutions_distinct_count_sum',
       'treatment_month', 'id', 'is_ls', 'is_ls_first', 'is_ls_last',
       'start_month', 'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total'],
      dtype='object')

In [44]:

# Sort the dataframe
combined_df = combined_df.sort_values(['id', 'publication_month'])

# Performance test
import time

start_time = time.time()

date_ranges = combined_df.drop_duplicates('id')[['id','start_month','end_month']].set_index('id')

# Create a DataFrame with all combinations of identifiers and months
all_months = pd.date_range(pd.to_datetime('2015-01-01'), combined_df['end_month'].max(), freq='MS')
complete_df = pd.DataFrame(
    index=pd.MultiIndex.from_product(
        [combined_df['id'].unique(), all_months],
        names=['id', 'publication_month']
    )
).reset_index()

# Merge with original data to keep actual observations
result = complete_df.merge(combined_df, on=['id', 'publication_month'], how='left')

# Filter out rows outside each identifier's date range
result = result[
    (result['publication_month'] >= result['id'].map(date_ranges['start_month'])) &
    (result['publication_month'] <= result['id'].map(date_ranges['end_month']))
]

end_time = time.time()

print(f"\nTime taken: {end_time - start_time:.4f} seconds")
print(f"Total rows in result: {len(result)}")


Time taken: 16.3625 seconds
Total rows in result: 7615108


In [46]:
with open('final_df_0828.pkl','wb') as file:
    pickle.dump(result, file)

In [3]:
with open('final_df_0828.pkl','rb') as file:
    result = pickle.load(file)

In [ ]:
result

In [4]:
def rolling_sum(cumsum, window):
    if len(cumsum) < window:
        # Create a series of NaN arrays with the same shape as the input arrays
        nan_array = np.full_like(cumsum.iloc[0], np.nan)
        return pd.Series([nan_array for _ in range(len(cumsum))])

    diff = cumsum.diff(window)
    # diff.iloc[window-1] = cumsum.iloc[window-1]
    return diff

In [7]:
columns_fill0 = ['count','af_count','2023 JIF_sum','5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum', 'Eigenfactor_sum', 'Normalized Eigenfactor_sum', 'Article Influence Score_sum', 'authors_count_sum', 'countries_distinct_count_sum', 'institutions_distinct_count_sum']
columns_ffill = ['treatment_month','is_ls','is_ls_first', 'is_ls_last', 'start_month',
       'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total']

def filldata(group):
    while group.iloc[0].isna()['count']:
        group = group.iloc[1:]
    group[columns_fill0] = group[columns_fill0].fillna(0)
    group[columns_ffill] = group[columns_ffill].ffill()

    # group['topics_unique'] = group['topic_portfolio_sum'].apply(np.count_nonzero)
    # group['subfields_unique'] = group['subfield_portfolio_sum'].apply(np.count_nonzero)
    # group['fields_unique'] = group['field_portfolio_sum'].apply(np.count_nonzero)
    # group['domains_unique'] = group['domain_portfolio_sum'].apply(np.count_nonzero)
    # group['topics_unique_3'] = rolling_sum(group['topic_portfolio_sum'],3).apply(np.count_nonzero)
    # group['subfields_unique_3'] = rolling_sum(group['subfield_portfolio_sum'],3).apply(np.count_nonzero)
    # group['fields_unique_3'] = rolling_sum(group['field_portfolio_sum'],3).apply(np.count_nonzero)
    # group['domains_unique_3'] = rolling_sum(group['domain_portfolio_sum'],3).apply(np.count_nonzero)
    # group['topics_unique_6'] = rolling_sum(group['topic_portfolio_sum'],6).apply(np.count_nonzero)
    # group['subfields_unique_6'] = rolling_sum(group['subfield_portfolio_sum'],6).apply(np.count_nonzero)
    # group['fields_unique_6'] = rolling_sum(group['field_portfolio_sum'],6).apply(np.count_nonzero)
    # group['domains_unique_6'] = rolling_sum(group['domain_portfolio_sum'],6).apply(np.count_nonzero)
    # group['topics_unique_12'] = rolling_sum(group['topic_portfolio_sum'],12).apply(np.count_nonzero)
    # group['subfields_unique_12'] = rolling_sum(group['subfield_portfolio_sum'],12).apply(np.count_nonzero)
    # group['fields_unique_12'] = rolling_sum(group['field_portfolio_sum'],12).apply(np.count_nonzero)
    # group['domains_unique_12'] = rolling_sum(group['domain_portfolio_sum'],12).apply(np.count_nonzero)
    
    # group['topics_hhi_3'] = rolling_sum(group['topic_portfolio_sum'],3).apply(hhi)
    # group['topics_hhi_6'] = rolling_sum(group['topic_portfolio_sum'],6).apply(hhi)
    # group['topics_hhi_12'] = rolling_sum(group['topic_portfolio_sum'],12).apply(hhi)
    
    # group['subfields_hhi_3'] = rolling_sum(group['subfield_portfolio_sum'],3).apply(hhi)
    # group['subfields_hhi_6'] = rolling_sum(group['subfield_portfolio_sum'],6).apply(hhi)
    # group['subfields_hhi_12'] = rolling_sum(group['subfield_portfolio_sum'],12).apply(hhi)
    
    # group['fields_hhi_3'] = rolling_sum(group['field_portfolio_sum'],3).apply(hhi)
    # group['fields_hhi_6'] = rolling_sum(group['field_portfolio_sum'],6).apply(hhi)
    # group['fields_hhi_12'] = rolling_sum(group['field_portfolio_sum'],12).apply(hhi)
    
    # group['domains_hhi_3'] = rolling_sum(group['domain_portfolio_sum'],3).apply(hhi)
    # group['domains_hhi_6'] = rolling_sum(group['domain_portfolio_sum'],6).apply(hhi)
    # group['domains_hhi_12'] = rolling_sum(group['domain_portfolio_sum'],12).apply(hhi)

    # for column in columns_fill0:
    #     group[f'{column}_3'] = group[column].rolling(3).mean()
    #     group[f'{column}_6'] = group[column].rolling(6).mean()
    #     group[f'{column}_12'] = group[column].rolling(12).mean()

    return group

# result_final = result.groupby('identifier', group_keys=False).apply(fill_publication_month)

    

In [5]:
columns_fill0 = ['count','af_count','2023 JIF_sum','5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum', 'Eigenfactor_sum', 'Normalized Eigenfactor_sum', 'Article Influence Score_sum', 'authors_count_sum', 'countries_distinct_count_sum', 'institutions_distinct_count_sum']
columns_ffill = ['treatment_month','is_ls','is_ls_first', 'is_ls_last', 'start_month',
       'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total']
levels = ['topic','subfield','field','domain']

def filldata(group):
    while group.iloc[0].isna()['count']:
        group = group.iloc[1:]
    group[columns_fill0] = group[columns_fill0].fillna(0)
    group[columns_ffill] = group[columns_ffill].ffill()


    topic_port = group['topic_portfolio_sum']
    subfield_port = group['subfield_portfolio_sum']
    field_port = group['field_portfolio_sum']
    domain_port = group['domain_portfolio_sum']
    topic_port_3 = rolling_sum(topic_port,3)
    topic_port_6 = rolling_sum(topic_port,6)
    topic_port_12 = rolling_sum(topic_port,12)
    subfield_port_3 = rolling_sum(subfield_port,3)
    subfield_port_6 = rolling_sum(subfield_port,6)
    subfield_port_12 = rolling_sum(subfield_port,12)
    field_port_3 = rolling_sum(field_port,3)
    field_port_6 = rolling_sum(field_port,6)
    field_port_12 = rolling_sum(field_port,12)
    domain_port_3 = rolling_sum(domain_port,3)
    domain_port_6 = rolling_sum(domain_port,6)
    domain_port_12 = rolling_sum(domain_port,12)
    group['topics_unique'] = topic_port.apply(np.count_nonzero)
    group['subfields_unique'] = subfield_port.apply(np.count_nonzero)
    group['fields_unique'] = field_port.apply(np.count_nonzero)
    group['domains_unique'] = domain_port.apply(np.count_nonzero)
    group['topics_unique_3'] = topic_port_3.apply(np.count_nonzero)
    group['subfields_unique_3'] = subfield_port_3.apply(np.count_nonzero)
    group['fields_unique_3'] = field_port_3.apply(np.count_nonzero)
    group['domains_unique_3'] = domain_port_3.apply(np.count_nonzero)
    group['topics_unique_6'] = topic_port_6.apply(np.count_nonzero)
    group['subfields_unique_6'] = subfield_port_6.apply(np.count_nonzero)
    group['fields_unique_6'] = field_port_6.apply(np.count_nonzero)
    group['domains_unique_6'] = domain_port_6.apply(np.count_nonzero)
    group['topics_unique_12'] = topic_port_12.apply(np.count_nonzero)
    group['subfields_unique_12'] = subfield_port_12.apply(np.count_nonzero)
    group['fields_unique_12'] = field_port_12.apply(np.count_nonzero)
    group['domains_unique_12'] = domain_port_12.apply(np.count_nonzero)
    
    group['topics_hhi_3'] = topic_port_3.apply(hhi)
    group['topics_hhi_6'] = topic_port_6.apply(hhi)
    group['topics_hhi_12'] = topic_port_12.apply(hhi)
    
    group['subfields_hhi_3'] = subfield_port_3.apply(hhi)
    group['subfields_hhi_6'] = subfield_port_6.apply(hhi)
    group['subfields_hhi_12'] = subfield_port_12.apply(hhi)
    
    group['fields_hhi_3'] = field_port_3.apply(hhi)
    group['fields_hhi_6'] = field_port_6.apply(hhi)
    group['fields_hhi_12'] = field_port_12.apply(hhi)
    
    group['domains_hhi_3'] = domain_port_3.apply(hhi)
    group['domains_hhi_6'] = domain_port_6.apply(hhi)
    group['domains_hhi_12'] = domain_port_12.apply(hhi)

    for column in columns_fill0:
        column_value = group[column]
        group[f'{column}_3'] = column_value.rolling(3).mean()
        group[f'{column}_6'] = column_value.rolling(6).mean()
        group[f'{column}_12'] = column_value.rolling(12).mean()

    return group

# result_final = result.groupby('identifier', group_keys=False).apply(fill_publication_month)

    

In [6]:
import warnings
warnings.filterwarnings('ignore')

In [7]:
result['id'].nunique()

83381

In [7]:
print('a')
def process_group(group_data):
    identifier, group = group_data
    return identifier, filldata(group)

def fill_publication_month_parallel(result, num_threads=10):
    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        futures = []
        for identifier, group in result.groupby('id'):
            futures.append(executor.submit(process_group, (identifier, group)))
        
        results = {}
        for future in tqdm(as_completed(futures), total=len(futures), desc="Processing groups"):
            identifier, processed_group = future.result()
            results[identifier] = processed_group
    
    return pd.concat(results.values())

# Usage
result_final = fill_publication_month_parallel(result)
with open('final_df_0828_2.pkl','wb') as file:
    pickle.dump(result_final, file)

a


Processing groups:  16%|█▋        | 13728/83381 [36:58<2:03:38,  9.39it/s] IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [12]:
result_final = result.groupby('id', group_keys=False).apply(filldata)

https://openalex.org/A5000001503
https://openalex.org/A5000003497
https://openalex.org/A5000004024
https://openalex.org/A5000004678
https://openalex.org/A5000006031
https://openalex.org/A5000007804


/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) 

https://openalex.org/A5000008953
https://openalex.org/A5000009346
https://openalex.org/A5000010047
https://openalex.org/A5000013516
https://openalex.org/A5000014202
https://openalex.org/A5000015913


/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) 

https://openalex.org/A5000016575
https://openalex.org/A5000018755
https://openalex.org/A5000019015
https://openalex.org/A5000022218
https://openalex.org/A5000024586
https://openalex.org/A5000026922
https://openalex.org/A5000028511


...

https://openalex.org/A5011840042
https://openalex.org/A5011842676
https://openalex.org/A5011844837
https://openalex.org/A5011846668
https://openalex.org/A5011847328
https://openalex.org/A5011850724


/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) 

https://openalex.org/A5011851211
https://openalex.org/A5011852238
https://openalex.org/A5011852805
https://openalex.org/A5011853443
https://openalex.org/A5011855276


/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  group[columns_ffill] = group[columns_ffill].ffill()
/state/partition1/job-50331405/ipykernel_1343885/1361465461.py:13: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) 

KeyboardInterrupt: 

In [11]:
test

id publication_month  count  af_count  \
0    https://openalex.org/A5000001503        2015-01-01    NaN       NaN   
1    https://openalex.org/A5000001503        2015-02-01    1.0       0.0   
2    https://openalex.org/A5000001503        2015-03-01    NaN       NaN   
3    https://openalex.org/A5000001503        2015-04-01    NaN       NaN   
4    https://openalex.org/A5000001503        2015-05-01    1.0       0.0   
..                                ...               ...    ...       ...   
206  https://openalex.org/A5000003497        2022-08-01    NaN       NaN   
207  https://openalex.org/A5000003497        2022-09-01    1.0       0.0   
208  https://openalex.org/A5000003497        2022-10-01    1.0       0.0   
209  https://openalex.org/A5000003497        2022-11-01    NaN       NaN   
210  https://openalex.org/A5000003497        2022-12-01    NaN       NaN   

     2023 JIF_sum  5 Year JIF_sum  Immediacy Index_sum  2023 JCI_sum  \
0             NaN             NaN                  NaN           NaN   
1            12.5            13.1                  2.3          2.87   
2             NaN             NaN                  NaN           NaN   
3             NaN             NaN                  NaN           NaN   
4             3.2             2.8                  0.8          0.69   
..            ...             ...                  ...           ...   
206           NaN             NaN                  NaN           NaN   
207           5.1             5.0                  1.1          1.45   
208           5.7             6.8                  1.1          0.95   
209           NaN             NaN                  NaN           NaN   
210           NaN             NaN                  NaN           NaN   

     Eigenfactor_sum  Normalized Eigenfactor_sum  ...  \
0                NaN                         NaN  ...   
1              0.037                       8.171  ...   
2                NaN                         NaN  ...   
3                NaN                         NaN  ...   
4              0.006                       1.377  ...   
..               ...                         ...  ...   
206              NaN                         NaN  ...   
207            0.009                       2.053  ...   
208            0.322                      70.448  ...   
209              NaN                         NaN  ...   
210              NaN                         NaN  ...   

                                subfield_portfolio_sum       subfield_max  \
0                                                  NaN                NaN   
1    [1, 1, 2, 5, 3, 1, 1, 1, 0, 6, 1, 14, 1, 1, 30...  Molecular Biology   
2                                                  NaN                NaN   
3                                                  NaN                NaN   
4    [1, 1, 2, 5, 3, 1, 1, 1, 0, 6, 1, 14, 1, 1, 31...  Molecular Biology   
..                                                 ...                ...   
206                                                NaN                NaN   
207                  [0, 1, 1, 1, 1, 1, 4, 0, 0, 1, 1]           Oncology   
208                  [0, 1, 1, 2, 1, 1, 4, 0, 0, 1, 1]           Oncology   
209                                                NaN                NaN   
210                                                NaN                NaN   

                field_portfolio_sum  \
0                               NaN   
1    [3, 46, 1, 1, 14, 1, 21, 4, 2]   
2                               NaN   
3                               NaN   
4    [3, 47, 1, 1, 14, 1, 21, 4, 2]   
..                              ...   
206                             NaN   
207              [1, 1, 1, 1, 6, 1]   
208              [1, 1, 2, 1, 6, 1]   
209                             NaN   
210                             NaN   

                                        field_max domain_portfolio_sum  \
0                                             NaN                  NaN   
1    Biochemistry, Genetics an

In [13]:
rolling_sum(test['topic_portfolio_sum'],3).apply(np.count_nonzero)

0       1
1       1
2       1
3       1
4       1
       ..
206     1
207     3
208     2
209     1
210    13
Name: topic_portfolio_sum, Length: 200, dtype: int64

In [17]:
test['topic_portfolio_sum'] = test['topic_portfolio_sum'].ffill()

In [19]:
test = result[result['id']==result['id'][0]]

In [15]:
test['topic_portfolio_sum'].diff(3)

0                                                    NaN
1                                                    NaN
2                                                    NaN
3                                                    NaN
4      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...
                             ...                        
206                                                  NaN
207              [1, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
208              [0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0]
209                                                  NaN
210    [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...
Name: topic_portfolio_sum, Length: 200, dtype: object

In [20]:
filldata(test)

id publication_month  count  af_count  \
1    https://openalex.org/A5000001503        2015-02-01    1.0       0.0   
2    https://openalex.org/A5000001503        2015-03-01    0.0       0.0   
3    https://openalex.org/A5000001503        2015-04-01    0.0       0.0   
4    https://openalex.org/A5000001503        2015-05-01    1.0       0.0   
5    https://openalex.org/A5000001503        2015-06-01    0.0       0.0   
..                                ...               ...    ...       ...   
99   https://openalex.org/A5000001503        2023-04-01    0.0       0.0   
100  https://openalex.org/A5000001503        2023-05-01    0.0       0.0   
101  https://openalex.org/A5000001503        2023-06-01    1.0       1.0   
102  https://openalex.org/A5000001503        2023-07-01    0.0       0.0   
103  https://openalex.org/A5000001503        2023-08-01    1.0       1.0   

     2023 JIF_sum  5 Year JIF_sum  Immediacy Index_sum  2023 JCI_sum  \
1            12.5            13.1                  2.3          2.87   
2             0.0             0.0                  0.0          0.00   
3             0.0             0.0                  0.0          0.00   
4             3.2             2.8                  0.8          0.69   
5             0.0             0.0                  0.0          0.00   
..            ...             ...                  ...           ...   
99            0.0             0.0                  0.0          0.00   
100           0.0             0.0                  0.0          0.00   
101           6.2             7.7                  1.1          0.94   
102           0.0             0.0                  0.0          0.00   
103           7.7             7.7                  1.7          1.47   

     Eigenfactor_sum  Normalized Eigenfactor_sum  ...  \
1              0.037                       8.171  ...   
2              0.000                       0.000  ...   
3              0.000                       0.000  ...   
4              0.006                       1.377  ...   
5              0.000                       0.000  ...   
..               ...                         ...  ...   
99             0.000                       0.000  ...   
100            0.000                       0.000  ...   
101            0.033                       7.230  ...   
102            0.000                       0.000  ...   
103            0.120                      26.132  ...   

     Article Influence Score_sum_12  authors_count_sum_3  authors_count_sum_6  \
1                               NaN                  NaN                  NaN   
2                               NaN                  NaN                  NaN   
3                               NaN             0.666667                  NaN   
4                               NaN             8.000000                  NaN   
5                               NaN             8.000000                  NaN   
..                              ...                  ...                  ...   
99                         2.278000             6.666667            43.000000   
100                        2.278000             5.000000            43.000000   
101                        2.447417             1.000000            43.500000   
102                        2.447417             1.000000             3.833333   
103                        2.528167             5.000000             5.000000   

     authors_count_sum_12 countries_distinct_count_sum_3  \
1                     NaN                            NaN   
2                     NaN                            NaN   
3                     NaN                       0.333333   
4                     NaN                       1.333333   
5                     NaN                       1.333333   
..                    ...                            ...   
99                  25.75                       1.333333   
100                 25.75                       1.000000   
101                 26.00                       0.666667   

In [12]:
result_final.columns

Index(['id', 'publication_month', 'count', 'af_count', '2023 JIF_sum',
       '5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum',
       'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
       'Article Influence Score_sum', 'authors_count_sum',
       'countries_distinct_count_sum', 'institutions_distinct_count_sum',
       'treatment_month', 'is_ls', 'is_ls_first', 'is_ls_last', 'start_month',
       'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total',
       'topics_unique', 'subfields_unique', 'fields_unique', 'domains_unique',
       'topics_unique_3', 'subfields_unique_3', 'fields_unique_3',
       'domains_unique_3', 'topics_unique_6', 'subfields_unique_6',
       'fields_unique_6', 'domains_unique_6', 'topics_unique_12',
       'subfields_unique_12', 'fields_unique

In [13]:
result_final.drop(columns={'topic_portfolio_sum','subfield_portfolio_sum','field_portfolio_sum','domain_portfolio_sum'}).to_stata('alphafold.dta', version=118)

In [18]:
result_final['id'].str.split('A')

18608      [https://openalex.org/, 5000199400]
18609      [https://openalex.org/, 5000199400]
18610      [https://openalex.org/, 5000199400]
18611      [https://openalex.org/, 5000199400]
18612      [https://openalex.org/, 5000199400]
                          ...                 
9588810    [https://openalex.org/, 9999999999]
9588811    [https://openalex.org/, 9999999999]
9588812    [https://openalex.org/, 9999999999]
9588813    [https://openalex.org/, 9999999999]
9588814    [https://openalex.org/, 9999999999]
Name: id, Length: 6995725, dtype: object

In [20]:
result_final['id_numeric'] = result_final['id'].str.split('A').apply(lambda x: x[1])

In [36]:
result_final['months_from_treatment'] = result_final['publication_month'].dt.year * 12 + result_final['publication_month'].dt.month - result_final['treatment_month'].dt.year * 12 - result_final['treatment_month'].dt.month

In [37]:
result_final = result_final.drop(columns={'topic_portfolio_sum','subfield_portfolio_sum','field_portfolio_sum','domain_portfolio_sum'})

In [38]:
result_final.to_stata('alphafold.dta',version=118)

In [41]:
result_final[result_final['domain_max']=='Life Sciences']

id publication_month  count  af_count  \
18608    https://openalex.org/A5000199400        2022-10-01    1.0       0.0   
18609    https://openalex.org/A5000199400        2022-11-01    0.0       0.0   
18610    https://openalex.org/A5000199400        2022-12-01    0.0       0.0   
18611    https://openalex.org/A5000199400        2023-01-01    1.0       1.0   
18612    https://openalex.org/A5000199400        2023-02-01    0.0       0.0   
...                                   ...               ...    ...       ...   
9588694  https://openalex.org/A5105003518        2024-02-01    0.0       0.0   
9588695  https://openalex.org/A5105003518        2024-03-01    4.0       0.0   
9588696  https://openalex.org/A5105003518        2024-04-01    0.0       0.0   
9588697  https://openalex.org/A5105003518        2024-05-01    0.0       0.0   
9588698  https://openalex.org/A5105003518        2024-06-01    2.0       0.0   

         2023 JIF_sum  5 Year JIF_sum  Immediacy Index_sum  2023 JCI_sum  \
18608             7.0             6.7                  1.2          1.80   
18609             0.0             0.0                  0.0          0.00   
18610             0.0             0.0                  0.0          0.00   
18611             2.7             3.6                  0.5          0.77   
18612             0.0             0.0                  0.0          0.00   
...               ...             ...                  ...           ...   
9588694           0.0             0.0                  0.0          0.00   
9588695          50.8            59.5                 10.9         12.95   
9588696           0.0             0.0                  0.0          0.00   
9588697           0.0             0.0                  0.0          0.00   
9588698          18.4            20.3                  3.4          4.24   

         Eigenfactor_sum  Normalized Eigenfactor_sum  ...  \
18608              0.032                       6.921  ...   
18609              0.000                       0.000  ...   
18610              0.000                       0.000  ...   
18611              0.006                       1.413  ...   
18612              0.000                       0.000  ...   
...                  ...                         ...  ...   
9588694            0.000                       0.000  ...   
9588695            1.529                     333.956  ...   
9588696            0.000                       0.000  ...   
9588697            0.000                       0.000  ...   
9588698            1.471                     321.346  ...   

         authors_count_sum_6  authors_count_sum_12  \
18608                    NaN                   NaN   
18609                    NaN                   NaN   
18610                    NaN                   NaN   
18611                    NaN                   NaN   
18612                    NaN                   NaN   
...                      ...                   ...   
9588694             6.333333             13.083333   
9588695            28.333333             21.083333   
9588696            26.333333             18.583333   
9588697            26.333333             16.583333   
9588698            25.666667             16.000000   

         countries_distinct_count_sum_3  countries_distinct_count_sum_6  \
18608                               NaN                             NaN   
18609                               NaN                             NaN   
18610                          0.333333                             NaN   
18611                          0.333333                             NaN   
18612                          0.333333                             NaN   
...                                 ...                             ...   
9588694                        2.000000                        1.166667   
9588695                        3.333333                        2.833333   
9588696                        3.333333                        2.666667   
9588697                        3.

In [59]:
result_final['months_from_start'] = result_final['publication_month'].dt.year * 12 + result_final['publication_month'].dt.month - result_final['start_month'].dt.year * 12 - result_final['start_month'].dt.month

In [47]:
with open('af_summary_0820.pkl','rb') as file:
    af_summary = pickle.load(file)

In [46]:
with open('author_info_0820.pkl','rb') as file:
    author_info = pickle.load(file)

In [57]:
result_final = result_final.merge(af_summary[['id','max_monthly_pubs','tenure','works_count','fuzzy_matched_name_count']], on='id', how='left')

In [52]:
author_info.columns

Index(['id', 'orcid', 'display_name', 'display_name_alternatives',
       'works_count', 'cited_by_count', 'summary_stats', 'ids', 'affiliations',
       'last_known_institutions', 'topics', 'topic_share', 'x_concepts',
       'counts_by_year', 'works_api_url', 'updated_date', 'created_date',
       'display_name_count', 'affiliations_count', 'countries_count',
       'name_normalized', 'namelist_normalized', 'normalized_name_count',
       'fuzzy_matched_name_count'],
      dtype='object')

In [55]:
author_info['last_known_institutions'].iloc[0]

[{'id': 'https://openalex.org/I183067930',
  'ror': 'https://ror.org/0220qvk04',
  'display_name': 'Shanghai Jiao Tong University',
  'country_code': 'CN',
  'type': 'education',
  'lineage': ['https://openalex.org/I183067930']},
 {'id': 'https://openalex.org/I4210144482',
  'ror': 'https://ror.org/049zrh188',
  'display_name': "Shanghai Sixth People's Hospital",
  'country_code': 'CN',
  'type': 'healthcare',
  'lineage': ['https://openalex.org/I4210144482']}]

In [56]:
af_summary

id adoption_month start_month  end_month  \
0      https://openalex.org/A5004395303     2022-07-01  2013-11-01 2024-06-01   
1      https://openalex.org/A5100774045     2023-12-01  2011-01-01 2024-05-01   
2      https://openalex.org/A5084998685     2024-02-01  2010-09-01 2024-02-01   
3      https://openalex.org/A5067704801     2024-04-01  2020-02-01 2024-04-01   
4      https://openalex.org/A5100436791     2023-01-01  1989-03-01 2024-08-01   
...                                 ...            ...         ...        ...   
84189  https://openalex.org/A5040334918     2023-10-01  2018-08-01 2023-10-01   
84190  https://openalex.org/A5100452754     2024-02-01  1990-01-01 2024-12-01   
84191  https://openalex.org/A5070884946     2023-10-01  2015-12-01 2023-10-01   
84192  https://openalex.org/A5042335469     2022-09-01  1997-09-01 2024-10-01   
84193  https://openalex.org/A5022064535     2023-06-01  2010-10-01 2024-07-01   

      pre_obs post_obs max_monthly_pubs tenure af_count  works_count  \
0        -104       23                1     10        1          6.0   
1        -155        5                3     13        1         30.0   
2        -161        0                3     13        1         32.0   
3         -50        0                1      4        1          6.0   
4        -406       19               14     35        1        663.0   
...       ...      ...              ...    ...      ...          ...   
84189     -62        0                2      5        1         13.0   
84190    -409       10                6     34        1        301.0   
84191     -94        0                2      7        1         13.0   
84192    -300       25                2     27        2        126.0   
84193    -152       13                3     13        1        127.0   

       display_name_count  affiliations_count  countries_count  \
0                     3.0                 3.0              1.0   
1                     3.0                 6.0              1.0   
2                     3.0                10.0              3.0   
3                     1.0                 2.0              2.0   
4                     4.0                10.0              2.0   
...                   ...                 ...              ...   
84189                 3.0                 4.0              2.0   
84190                 4.0                10.0              1.0   
84191                 3.0                 4.0              1.0   
84192                 2.0                 9.0              3.0   
84193                 1.0                10.0              5.0   

       normalized_name_count  fuzzy_matched_name_count  
0                        3.0                       1.0  
1                        3.0                       1.0  
2                        2.0                       1.0  
3                        1.0                       1.0  
4                        4.0                       1.0  
...                      ...                       ...  
84189                    3.0                       1.0  
84190                    4.0                       2.0  
84191                    3.0                       1.0  
84192                    2.0                       1.0  
84193                    1.0                       1.0  

[84194 rows x 15 columns]

In [63]:
result_final['max_monthly_pubs'] = result_final['max_monthly_pubs'].astype(int)

In [68]:
result_final = result_final.merge(af_summary[['id','pre_obs','post_obs']], on='id',how='left')

In [71]:
result_final['pre_obs'] = result_final['pre_obs'].astype(int)
result_final['post_obs'] = result_final['post_obs'].astype(int)

In [72]:
result_final.to_stata('alphafold.dta',version=118)

In [69]:
result_final.columns

Index(['id', 'publication_month', 'count', 'af_count', '2023 JIF_sum',
       '5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum',
       'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
       ...
       'institutions_distinct_count_sum_12', 'id_numeric',
       'months_from_treatment', 'max_monthly_pubs', 'tenure', 'works_count',
       'fuzzy_matched_name_count', 'months_from_start', 'pre_obs', 'post_obs'],
      dtype='object', length=101)

In [5]:
with open('final_df_0828_2.pkl','rb') as file:
    df = pickle.load(file)

In [6]:
df

id publication_month   count  af_count  \
18608    https://openalex.org/A5000199400        2022-10-01     1.0       0.0   
18609    https://openalex.org/A5000199400        2022-11-01     0.0       0.0   
18610    https://openalex.org/A5000199400        2022-12-01     0.0       0.0   
18611    https://openalex.org/A5000199400        2023-01-01     1.0       1.0   
18612    https://openalex.org/A5000199400        2023-02-01     0.0       0.0   
...                                   ...               ...     ...       ...   
9588810  https://openalex.org/A9999999999        2024-03-01   156.0       0.0   
9588811  https://openalex.org/A9999999999        2024-04-01   319.0       0.0   
9588812  https://openalex.org/A9999999999        2024-05-01  1118.0       1.0   
9588813  https://openalex.org/A9999999999        2024-06-01  2443.0       1.0   
9588814  https://openalex.org/A9999999999        2024-07-01  9162.0      24.0   

         2023 JIF_sum  5 Year JIF_sum  Immediacy Index_sum  2023 JCI_sum  \
18608             7.0             6.7                  1.2          1.80   
18609             0.0             0.0                  0.0          0.00   
18610             0.0             0.0                  0.0          0.00   
18611             2.7             3.6                  0.5          0.77   
18612             0.0             0.0                  0.0          0.00   
...               ...             ...                  ...           ...   
9588810          44.2            38.2                 13.9         12.85   
9588811          89.7            90.3                 31.9         24.09   
9588812          60.6            65.8                 11.1         16.64   
9588813       11967.8         10674.6               3694.3       1870.30   
9588814       31330.1         32514.0               7366.7       7348.91   

         Eigenfactor_sum  Normalized Eigenfactor_sum  ...  \
18608              0.032                       6.921  ...   
18609              0.000                       0.000  ...   
18610              0.000                       0.000  ...   
18611              0.006                       1.413  ...   
18612              0.000                       0.000  ...   
...                  ...                         ...  ...   
9588810            0.072                      16.838  ...   
9588811            0.107                      27.441  ...   
9588812            0.254                      56.465  ...   
9588813           58.461                   12800.084  ...   
9588814          530.454                  115887.084  ...   

         Article Influence Score_sum_12  authors_count_sum_3  \
18608                               NaN                  NaN   
18609                               NaN                  NaN   
18610                               NaN             3.000000   
18611                               NaN             2.333333   
18612                               NaN             2.333333   
...                                 ...                  ...   
9588810                       53.308833          3635.333333   
9588811                       54.698583           940.000000   
9588812                       55.787500          3479.666667   
9588813                      420.425083          6619.666667   
9588814                     1144.385083         23646.000000   

         authors_count_sum_6  authors_count_sum_12  \
18608                    NaN                   NaN   
18609                    NaN                   NaN   
18610                    NaN                   NaN   
18611                    NaN                   NaN   
18612                    NaN                   NaN   
...                      ...                   ...   
9588810          4402.833333           2277.500000   
9588811          2732.333333           2392.666667   
9588812          3435.500000           3027.083333   
9588813          5127.500000           3871.583333   
9588814         12293.000000           8290.666667   

  

In [7]:
print(df.columns)

Index(['id', 'publication_month', 'count', 'af_count', '2023 JIF_sum',
       '5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum',
       'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
       'Article Influence Score_sum', 'authors_count_sum',
       'countries_distinct_count_sum', 'institutions_distinct_count_sum',
       'treatment_month', 'is_ls', 'is_ls_first', 'is_ls_last', 'start_month',
       'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total',
       'topics_unique', 'subfields_unique', 'fields_unique', 'domains_unique',
       'topics_unique_3', 'subfields_unique_3', 'fields_unique_3',
       'domains_unique_3', 'topics_unique_6', 'subfields_unique_6',
       'fields_unique_6', 'domains_unique_6', 'topics_unique_12',
       'subfields_unique_12', 'fields_unique

In [8]:
df[df['is_ls']]

id publication_month   count  af_count  \
18608    https://openalex.org/A5000199400        2022-10-01     1.0       0.0   
18609    https://openalex.org/A5000199400        2022-11-01     0.0       0.0   
18610    https://openalex.org/A5000199400        2022-12-01     0.0       0.0   
18611    https://openalex.org/A5000199400        2023-01-01     1.0       1.0   
18612    https://openalex.org/A5000199400        2023-02-01     0.0       0.0   
...                                   ...               ...     ...       ...   
9588810  https://openalex.org/A9999999999        2024-03-01   156.0       0.0   
9588811  https://openalex.org/A9999999999        2024-04-01   319.0       0.0   
9588812  https://openalex.org/A9999999999        2024-05-01  1118.0       1.0   
9588813  https://openalex.org/A9999999999        2024-06-01  2443.0       1.0   
9588814  https://openalex.org/A9999999999        2024-07-01  9162.0      24.0   

         2023 JIF_sum  5 Year JIF_sum  Immediacy Index_sum  2023 JCI_sum  \
18608             7.0             6.7                  1.2          1.80   
18609             0.0             0.0                  0.0          0.00   
18610             0.0             0.0                  0.0          0.00   
18611             2.7             3.6                  0.5          0.77   
18612             0.0             0.0                  0.0          0.00   
...               ...             ...                  ...           ...   
9588810          44.2            38.2                 13.9         12.85   
9588811          89.7            90.3                 31.9         24.09   
9588812          60.6            65.8                 11.1         16.64   
9588813       11967.8         10674.6               3694.3       1870.30   
9588814       31330.1         32514.0               7366.7       7348.91   

         Eigenfactor_sum  Normalized Eigenfactor_sum  ...  \
18608              0.032                       6.921  ...   
18609              0.000                       0.000  ...   
18610              0.000                       0.000  ...   
18611              0.006                       1.413  ...   
18612              0.000                       0.000  ...   
...                  ...                         ...  ...   
9588810            0.072                      16.838  ...   
9588811            0.107                      27.441  ...   
9588812            0.254                      56.465  ...   
9588813           58.461                   12800.084  ...   
9588814          530.454                  115887.084  ...   

         Article Influence Score_sum_12  authors_count_sum_3  \
18608                               NaN                  NaN   
18609                               NaN                  NaN   
18610                               NaN             3.000000   
18611                               NaN             2.333333   
18612                               NaN             2.333333   
...                                 ...                  ...   
9588810                       53.308833          3635.333333   
9588811                       54.698583           940.000000   
9588812                       55.787500          3479.666667   
9588813                      420.425083          6619.666667   
9588814                     1144.385083         23646.000000   

         authors_count_sum_6  authors_count_sum_12  \
18608                    NaN                   NaN   
18609                    NaN                   NaN   
18610                    NaN                   NaN   
18611                    NaN                   NaN   
18612                    NaN                   NaN   
...                      ...                   ...   
9588810          4402.833333           2277.500000   
9588811          2732.333333           2392.666667   
9588812          3435.500000           3027.083333   
9588813          5127.500000           3871.583333   
9588814         12293.000000           8290.666667   

  

In [9]:
with open('af_citing_works_0725.pkl', 'rb') as file:
    af_citing_works = pickle.load(file)

In [10]:
domains = af_citing_works['primary_topic'].apply(lambda x: x['domain']['display_name'] if x is not None else None)

In [12]:
af_citing_ls = af_citing_works[domains=='Life Sciences']

In [13]:
af_citing_ls

id  \
0      https://openalex.org/W3211795435   
1      https://openalex.org/W4281790889   
2      https://openalex.org/W3183475563   
3      https://openalex.org/W4327550249   
4      https://openalex.org/W4308616064   
...                                 ...   
14202  https://openalex.org/W4285314705   
14203  https://openalex.org/W4285344452   
14205  https://openalex.org/W3214914650   
14206  https://openalex.org/W3215803257   
14208  https://openalex.org/W4285347087   

                                                   doi  \
0                 https://doi.org/10.1093/nar/gkab1061   
1           https://doi.org/10.1038/s41592-022-01488-1   
2           https://doi.org/10.1038/s41586-021-03828-1   
3              https://doi.org/10.1126/science.ade2574   
4                  https://doi.org/10.1093/nar/gkac993   
...                                                ...   
14202              https://doi.org/10.4000/netcom.6329   
14203              https://doi.org/10.4000/netcom.6194   
14205             https://doi.org/10.2139/ssrn.3967674   
14206           https://doi.org/10.2142/biophys.61.410   
14208  https://doi.org/10.33965/icwi_ac2021_202109l014   

                                                   title  \
0      AlphaFold Protein Structure Database: massivel...   
1      ColabFold: making protein folding accessible t...   
2      Highly accurate protein structure prediction f...   
3      Evolutionary-scale prediction of atomic-level ...   
4                                       InterPro in 2022   
...                                                  ...   
14202  Réflexions suite au 57e colloque de l’ASRDLF «...   
14203  Réflexions suite au 57e colloque de l’ASRDLF «...   
14205  Rational Exploration of Fold Atlas for Human S...   
14206  Discussion Commemorating the 60th Anniversary ...   
14208  PARALLEL BACKTRACKING FOR THE STUDY OF THE HYD...   

                                            display_name  publication_year  \
0      AlphaFold Protein Structure Database: massivel...              2021   
1      ColabFold: making protein folding accessible t...              2022   
2      Highly accurate protein structure prediction f...              2021   
3      Evolutionary-scale prediction of atomic-level ...              2023   
4                                       InterPro in 2022              2022   
...                                                  ...               ...   
14202  Réflexions suite au 57e colloque de l’ASRDLF «...              2021   
14203  Réflexions suite au 57e colloque de l’ASRDLF «...              2021   
14205  Rational Exploration of Fold Atlas for Human S...              2021   
14206  Discussion Commemorating the 60th Anniversary ...              2021   
14208  PARALLEL BACKTRACKING FOR THE STUDY OF THE HYD...              2021   

      publication_date                                                ids  \
0           2021-11-17  {'openalex': 'https://openalex.org/W3211795435...   
1           2022-05-30  {'openalex': 'https://openalex.org/W4281790889...   
2           2021-07-22  {'openalex': 'https://openalex.org/W3183475563...   
3           2023-03-17  {'openalex': 'https://openalex.org/W4327550249...   
4           2022-11-09  {'openalex': 'https://openalex.org/W4308616064...   
...                ...                                                ...   
14202       2021-12-30  {'openalex': 'https://openalex.org/W4285314705...   
14203       2021-10-20  {'openalex': 'https://openalex.org/W4285344452...   
14205       2021-01-01  {'openalex': 'https://openalex.org/W3214914650...   
14206       2021-01-01  {'openalex': 'https://openalex.org/W3215803257...   
14208       2021-10-13  {'openalex': 'https://openalex.org/W4285347087...   

      language                                   primary_location     type  \
0           en  {'is_oa': True, 'landing_page_url': 'https://d...  article   
1           en  {'is_oa': True, 'landing_page_url': 'https://d...  article   
2     

In [14]:
with open('ls_authors.pkl','rb') as file:
    ls_authors = pickle.load(file)

In [17]:
print(df.columns)

Index(['id', 'publication_month', 'count', 'af_count', '2023 JIF_sum',
       '5 Year JIF_sum', 'Immediacy Index_sum', '2023 JCI_sum',
       'Eigenfactor_sum', 'Normalized Eigenfactor_sum',
       'Article Influence Score_sum', 'authors_count_sum',
       'countries_distinct_count_sum', 'institutions_distinct_count_sum',
       'treatment_month', 'is_ls', 'is_ls_first', 'is_ls_last', 'start_month',
       'end_month', 'topic_portfolio_sum', 'topic_max',
       'subfield_portfolio_sum', 'subfield_max', 'field_portfolio_sum',
       'field_max', 'domain_portfolio_sum', 'domain_max', 'topic_hhi_total',
       'subfield_hhi_total', 'field_hhi_total', 'domain_hhi_total',
       'topics_unique', 'subfields_unique', 'fields_unique', 'domains_unique',
       'topics_unique_3', 'subfields_unique_3', 'fields_unique_3',
       'domains_unique_3', 'topics_unique_6', 'subfields_unique_6',
       'fields_unique_6', 'domains_unique_6', 'topics_unique_12',
       'subfields_unique_12', 'fields_unique

In [18]:
df = pd.read_stata('alphafold_ls_24.dta')

In [19]:
df

index                                id publication_month  count  \
0          26628  https://openalex.org/A5000001503        2020-01-01    0.0   
1          26629  https://openalex.org/A5000001503        2020-02-01    0.0   
2          26630  https://openalex.org/A5000001503        2020-03-01    0.0   
3          26631  https://openalex.org/A5000001503        2020-04-01    0.0   
4          26632  https://openalex.org/A5000001503        2020-05-01    0.0   
...          ...                               ...               ...    ...   
1420472  6995081  https://openalex.org/A5104992075        2022-12-01    0.0   
1420473  6995082  https://openalex.org/A5104992075        2023-01-01    0.0   
1420474  6995083  https://openalex.org/A5104992075        2023-02-01    0.0   
1420475  6995084  https://openalex.org/A5104992075        2023-03-01    0.0   
1420476  6995085  https://openalex.org/A5104992075        2023-04-01    0.0   

         af_count  _2023_JIF_sum  _5_Year_JIF_sum  Immediacy_Index_sum  \
0             0.0            0.0              0.0                  0.0   
1             0.0            0.0              0.0                  0.0   
2             0.0            0.0              0.0                  0.0   
3             0.0            0.0              0.0                  0.0   
4             0.0            0.0              0.0                  0.0   
...           ...            ...              ...                  ...   
1420472       0.0            0.0              0.0                  0.0   
1420473       0.0            0.0              0.0                  0.0   
1420474       0.0            0.0              0.0                  0.0   
1420475       0.0            0.0              0.0                  0.0   
1420476       0.0            0.0              0.0                  0.0   

         _2023_JCI_sum  Eigenfactor_sum  ...  obs_12  obs_24  \
0                  0.0              0.0  ...       0       1   
1                  0.0              0.0  ...       0       1   
2                  0.0              0.0  ...       0       1   
3                  0.0              0.0  ...       0       1   
4                  0.0              0.0  ...       0       1   
...                ...              ...  ...     ...     ...   
1420472            0.0              0.0  ...       1       1   
1420473            0.0              0.0  ...       1       1   
1420474            0.0              0.0  ...       1       1   
1420475            0.0              0.0  ...       1       1   
1420476            0.0              0.0  ...       1       1   

         topic_hhi_adjusted  topic_hhi_adjusted_diff  subfield_hhi_adjusted  \
0                 -0.454958                      NaN              -0.260166   
1                 -0.454958                      0.0              -0.260166   
2                 -0.454958                      0.0              -0.260166   
3                 -0.454958                      0.0              -0.260166   
4                 -0.454958                      0.0              -0.260166   
...                     ...                      ...                    ...   
1420472           -0.005926                      0.0               0.170370   
1420473           -0.005926                      0.0               0.170370   
1420474           -0.005926                      0.0               0.170370   
1420475           -0.005926                      0.0               0.170370   
1420476           -0.005926                      0.0               0.170370   

        subfield_hhi_adjusted_diff  field_hhi_adjusted  \
0                              NaN           -0.014515   
1                              0.0           -0.014515   
2                              0.0           -0.014515   
3                              0.0           -0.014515   
4                              0.0           -0.014515   
...                            ...                 ...   
1420472                        0.0            0.3

In [20]:
df.groupby('domain').id.nunique()

/state/partition1/job-50597248/ipykernel_2386496/2493470856.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  df.groupby('domain').id.nunique()


domain
Health Sciences       6919
Life Sciences        32462
Physical Sciences     5506
Social Sciences        241
Name: id, dtype: int64

In [29]:
pd.DataFrame(df.groupby('field').id.nunique()).reset_index().sort_values('id', ascending=False)

/state/partition1/job-50597248/ipykernel_2386496/1962310623.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  pd.DataFrame(df.groupby('field').id.nunique()).reset_index().sort_values('id', ascending=False)


field     id
2   Biochemistry, Genetics and Molecular Biology  26653
18                                      Medicine   7428
0           Agricultural and Biological Sciences   3941
15                   Immunology and Microbiology   1360
12                                   Engineering   1317
6                               Computer Science    842
19                                  Neuroscience    751
5                                      Chemistry    724
16                             Materials Science    612
13                         Environmental Science    607
22                         Physics and Astronomy    259
11                                        Energy    107
24                               Social Sciences    100
9                   Earth and Planetary Sciences     93
21    Pharmacology, Toxicology and Pharmaceutics     54
23                                    Psychology     48
20                                       Nursing     34
1                            Arts and Humanities     33
3            Business, Management and Accounting     28
10           Economics, Econometrics and Finance     26
17                                   Mathematics     26
8                                      Dentistry     20
14                            Health Professions     19
7                              Decision Sciences     19
25                                    Veterinary     15
4                           Chemical Engineering     12

In [26]:
df['id'].nunique()

45144

In [30]:
45144-45128

16